In [1]:
from io import StringIO
from collections import Counter
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import math

from sklearn import tree
from sklearn.neighbors import KNeighborsClassifier
from sklearn.cross_validation import train_test_split
from sklearn.metrics import accuracy_score

import pydot_ng as pydot
from IPython.display import Image
from tabulate import tabulate
from operator import itemgetter, attrgetter

# Data Processing

## Load Data

In [2]:
df = pd.read_csv('./speed-dating-experiment/Speed Dating Data.csv', encoding="ISO-8859-1")

## Analyze Data

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8378 entries, 0 to 8377
Columns: 195 entries, iid to amb5_3
dtypes: float64(174), int64(13), object(8)
memory usage: 12.5+ MB


In [4]:
# Unparseable columns

unparseable_cols = df.select_dtypes(include=['object']).columns
unparseable_cols

Index(['field', 'undergra', 'mn_sat', 'tuition', 'from', 'zipcode', 'income',
       'career'],
      dtype='object')

In [5]:
# Number of null value of each columns

cols_to_null_nums = df.isnull().sum(axis=0).sort_values(ascending=False)
cols_to_null_nums

num_in_3    7710
numdat_3    6882
expnum      6578
sinc7_2     6423
amb7_2      6423
shar7_2     6404
intel7_2    6394
fun7_2      6394
attr7_2     6394
amb5_3      6362
shar7_3     6362
fun5_3      6362
sinc5_3     6362
attr7_3     6362
sinc7_3     6362
intel7_3    6362
fun7_3      6362
amb7_3      6362
attr5_3     6362
intel5_3    6362
shar2_3     6362
intel4_3    5419
sinc2_3     5419
amb2_3      5419
fun2_3      5419
intel2_3    5419
attr2_3     5419
shar4_3     5419
amb4_3      5419
fun4_3      5419
            ... 
clubbing      79
tv            79
art           79
tvsports      79
attr2_1       79
museums       79
go_out        79
sports        79
goal          79
exercise      79
dining        79
hiking        79
race_o        73
field         63
race          63
pid           10
id             1
round          0
gender         0
idg            0
condtn         0
wave           0
dec            0
position       0
order          0
partner        0
match          0
samerace      

In [6]:
# Number of null value of each row

rows_to_null_nums = df.isnull().sum(axis=1).sort_values(ascending=False)
rows_to_null_nums

842     172
847     172
845     172
839     172
843     172
838     171
324     158
841     155
846     154
840     154
844     154
314     150
313     150
321     150
316     149
315     149
322     149
317     149
319     149
320     149
312     149
318     149
323     149
326     149
325     149
327     149
829     149
828     141
833     139
831     139
       ... 
6746      2
6751      2
7273      2
6748      2
6747      2
7272      2
6466      2
6744      2
7270      2
7274      2
7269      2
7275      2
5885      2
6465      2
6464      2
6463      2
6462      2
6750      2
6906      1
6907      1
6919      1
6917      1
6908      1
6910      1
6912      1
6913      1
6920      1
6915      1
6916      1
6914      1
dtype: int64

In [7]:
df.describe()

/Users/nacat/anaconda3/lib/python3.5/site-packages/numpy/lib/function_base.py:3834: RuntimeWarning: Invalid value encountered in percentile
  RuntimeWarning)


iid           id       gender          idg       condtn  \
count  8378.000000  8377.000000  8378.000000  8378.000000  8378.000000   
mean    283.675937     8.960248     0.500597    17.327166     1.828837   
std     158.583367     5.491329     0.500029    10.940735     0.376673   
min       1.000000     1.000000     0.000000     1.000000     1.000000   
25%     154.000000          NaN     0.000000     8.000000     2.000000   
50%     281.000000          NaN     1.000000    16.000000     2.000000   
75%     407.000000          NaN     1.000000    26.000000     2.000000   
max     552.000000    22.000000     1.000000    44.000000     2.000000   

              wave        round     position     positin1        order  \
count  8378.000000  8378.000000  8378.000000  6532.000000  8378.000000   
mean     11.350919    16.872046     9.042731     9.295775     8.927668   
std       5.995903     4.358458     5.514939     5.650199     5.477009   
min       1.000000     5.000000     1.000000     1.000000     1.000000   
25%       7.000000    14.000000     4.000000          NaN     4.000000   
50%      11.000000    18.000000     8.000000          NaN     8.000000   
75%      15.000000    20.000000    13.000000          NaN    13.000000   
max      21.000000    22.000000    22.000000    22.000000    22.000000   

          ...           attr3_3      sinc3_3     intel3_3       fun3_3  \
count     ...       3974.000000  3974.000000  3974.000000  3974.000000   
mean      ...          7.240312     8.093357     8.388777     7.658782   
std       ...          1.576596     1.610309     1.459094     1.744670   
min       ...          2.000000     2.000000     3.000000     2.000000   
25%       ...               NaN          NaN          NaN          NaN   
50%       ...               NaN          NaN          NaN          NaN   
75%       ...               NaN          NaN          NaN          NaN   
max       ...         12.000000    12.000000    12.000000    12.000000   

            amb3_3      attr5_3      sinc5_3     intel5_3       fun5_3  \
count  3974.000000  2016.000000  2016.000000  2016.000000  2016.000000   
mean      7.391545     6.810020     7.615079     7.932540     7.155258   
std       1.961417     1.507341     1.504551     1.340868     1.672787   
min       1.000000     2.000000     2.000000     4.000000     1.000000   
25%            NaN          NaN          NaN          NaN          NaN   
50%            NaN          NaN          NaN          NaN          NaN   
75%            NaN          NaN          NaN          NaN          NaN   
max      12.000000    10.000000    10.000000    10.000000    10.000000   

            amb5_3  
count  2016.000000  
mean      7.048611  
std       1.717988  
min       1.000000  
25%            NaN  
50%            NaN  
75%            NaN  
max      10.000000  

[8 rows x 187 columns]

## Data Cleaning

In [8]:
# Clean Comma
COLUMNS_WITH_COMMA = ['income', 'zipcode', 'tuition', 'mn_sat']

for col in COLUMNS_WITH_COMMA:
    df[col] = df[col].replace('[,]', '', regex=True).astype(float)

### Drop Rows

In [9]:
# Cols with too many null values
# Total columns in each row: 195

ROW_NULL_VALUE_THRESHOLD = 100

rows_with_too_many_null = rows_to_null_nums[rows_to_null_nums > ROW_NULL_VALUE_THRESHOLD].index
df.drop(rows_with_too_many_null, axis=0, inplace=True)

### Drop Columns

In [10]:
STRING_COLUMNS = ['field', 'from', 'career', 'undergra']
REDUNDANT_COLUMNS = [
    # match
    'dec', 'dec_o'
]
ID_RELATED_COLUMNS = [
    'iid', 'id', 'idg', 'partner', 'pid'
]

In [11]:
# Drop rows with too many null values
# Totla cols in each rows: 8378

COL_NULL_VALUE_THRESHOLD = 4000

cols_with_too_many_null = cols_to_null_nums[cols_to_null_nums > COL_NULL_VALUE_THRESHOLD].index

In [12]:
col_to_drop_groups = [
    STRING_COLUMNS,
    REDUNDANT_COLUMNS,
    ID_RELATED_COLUMNS,
    cols_with_too_many_null
]

cols_to_drop = {col for col_group in col_to_drop_groups
                for col in col_group}
cols_to_drop

{'amb1_3',
 'amb1_s',
 'amb2_3',
 'amb3_3',
 'amb3_s',
 'amb4_3',
 'amb5_2',
 'amb5_3',
 'amb7_2',
 'amb7_3',
 'attr1_3',
 'attr1_s',
 'attr2_3',
 'attr3_3',
 'attr3_s',
 'attr4_3',
 'attr5_2',
 'attr5_3',
 'attr7_2',
 'attr7_3',
 'career',
 'date_3',
 'dec',
 'dec_o',
 'expnum',
 'field',
 'from',
 'fun1_3',
 'fun1_s',
 'fun2_3',
 'fun3_3',
 'fun3_s',
 'fun4_3',
 'fun5_2',
 'fun5_3',
 'fun7_2',
 'fun7_3',
 'id',
 'idg',
 'iid',
 'income',
 'intel1_3',
 'intel1_s',
 'intel2_3',
 'intel3_3',
 'intel3_s',
 'intel4_3',
 'intel5_2',
 'intel5_3',
 'intel7_2',
 'intel7_3',
 'mn_sat',
 'num_in_3',
 'numdat_3',
 'partner',
 'pid',
 'shar1_3',
 'shar1_s',
 'shar2_3',
 'shar4_3',
 'shar7_2',
 'shar7_3',
 'sinc1_3',
 'sinc1_s',
 'sinc2_3',
 'sinc3_3',
 'sinc3_s',
 'sinc4_3',
 'sinc5_2',
 'sinc5_3',
 'sinc7_2',
 'sinc7_3',
 'them_cal',
 'tuition',
 'undergra',
 'you_call'}

In [13]:
df.drop(cols_to_drop, axis=1, inplace=True)

### Fill NaN Values

In [14]:
# File NaN with 0

df.fillna(0, inplace=True)

## Split Data

In [15]:
df_X = df.drop('match', axis=1)
df_y = df['match']

X = np.array(df_X)
y = np.array(df_y)

In [16]:
train_X, test_X, train_y, test_y = train_test_split(X, y, test_size=0.2, random_state=1)

In [17]:
for feature, label in zip(train_X, train_y):
    print(feature,label)
    break

[  1.     2.     9.    20.    10.    14.    17.     0.03   0.    27.     3.
  14.29  18.37  18.37  16.33  18.37  14.29   6.     6.     7.     6.     6.
   5.     5.     6.     2.    25.    13.     6.     1.     1.     0.     1.
   5.     2.     6.     9.     9.     5.    10.     9.    10.    10.     6.
   8.    10.     2.     5.     5.     5.     9.     5.     5.    10.    16.67
  16.67  16.67  16.67  14.81  18.52   9.     8.     8.     9.     9.    10.
  15.38  15.38  15.38  17.31  17.31  19.23  10.    10.    10.    10.    10.
   0.     0.     0.     0.     0.     6.     8.     9.     9.     8.     9.
   9.     9.     2.    18.    10.     1.     1.    17.86  17.86  17.86
  17.86  14.29  14.29  10.     8.     8.     9.     9.    10.    16.95
  16.95  16.95  16.95  16.95  15.25  10.    10.    10.    10.    10.  ] 0


# KNN

## Self Implement

In [18]:
len(train_X) # number of tuple

6522

In [19]:
len(train_X[0]) # number of feauture 

118

In [20]:
def eucldn_similarity(v1, v2):
    """
    Euclidean Distance。越相似，距離越近，相似度數值會越小。
    :param v1:
    :param v2:
    :return: 1/distance(v1,v2) 取距離的倒數，越大越像
    """
    sum_xx, sum_xy, sum_yy = 0.0, 0.0, 0.0
    for i in range(0, len(v1)):
        sum_xx += math.pow(v1[i], 2)
        sum_xy += v1[i] * v2[i]
        sum_yy += math.pow(v2[i], 2)

    return 1/math.sqrt(sum_xx + sum_yy - 2*sum_xy)

In [21]:
def cos_similarity(v1, v2):
    """
    Cosine（兩向量的餘弦）。越相似，夾角越小，相似度數值會越高。
    :param v1:
    :param v2:
    :return: cos(v1,v2)介於1到-1之間 越大越像
    """
    sum_xx, sum_xy, sum_yy = 0.0, 0.0, 0.0
    for i in range(0, len(v1)):
        sum_xx += math.pow(v1[i], 2)
        sum_xy += v1[i] * v2[i]
        sum_yy += math.pow(v2[i], 2)
    return sum_xy / math.sqrt(sum_xx * sum_yy)

In [22]:
def prediction(nb_list):
    cnt = Counter()
    
    for tp in nb_list:
        cnt[tp[-1]] += 1
    label = cnt.most_common(1)[0][0]
    return label

In [23]:
def accuracy(nb_list):
    score = 0
    
    return score

In [24]:
def knn_classify(test_X, train_X, train_y, k=5):
    nb = []
    for feature, label in zip(train_X, train_y):
        nb.append((cos_similarity(test_X,feature),label))
    nb.sort(reverse=True)
    label = prediction(nb[:k])
    return label

In [37]:
count = 0
for feature, label in zip(test_X, test_y):
    pred_y = knn_classify(feature, train_X, train_y, 5)
    if pred_y == label:
        count += 1
accuracy = count / len(test_X)

In [36]:
accuracy

0.8136112814224402

## Sklearn

In [27]:
clf = KNeighborsClassifier(n_neighbors=5)
clf.fit(train_X, train_y)

KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
           metric_params=None, n_jobs=1, n_neighbors=5, p=2,
           weights='uniform')

In [28]:
pred = clf.predict(test_X)
accuracy_score(pred, test_y)

0.81545064377682408

# Decision Tree

## Self Implement

## Sklearn

In [29]:
clf = tree.DecisionTreeClassifier(min_samples_leaf=5)
clf.fit(train_X, train_y)

DecisionTreeClassifier(class_weight=None, criterion='gini', max_depth=None,
            max_features=None, max_leaf_nodes=None, min_samples_leaf=5,
            min_samples_split=2, min_weight_fraction_leaf=0.0,
            presort=False, random_state=None, splitter='best')

In [30]:
pred = clf.predict(test_X)
accuracy_score(pred, test_y)

0.79337829552421824

In [31]:
# Visualize Decision Tree

dot_data = StringIO()
tree.export_graphviz(clf, out_file=dot_data,
                     feature_names=df_X.columns, class_names=True)
graph = pydot.graph_from_dot_data(dot_data.getvalue())  
Image(graph.create_png())